# Interactive maps with Folium

- https://kodu.ut.ee/~kmoch/geopython2019/L6/interactive-map-folium.html

In [19]:
import folium

# Create a Map instance
m = folium.Map(location=[58.37, 26.72], zoom_start=11, control_scale=True)



In [20]:
m

In [2]:
# Filepath to the output
outfp = "base_map.html"

# Save the map
m.save(outfp)

In [23]:
# Let's change the basemap style to 'Stamen Toner'
m = folium.Map(location=[58.37, 26.72], tiles='CartoDB positron', zoom_start=12, control_scale=True, prefer_canvas=True)
m

In [24]:
import geopandas as gpd
from fiona.crs import from_epsg
from shapely.geometry import LineString, MultiLineString

# Filepaths
grid_fp = "population_square_km.shp"
roads_fp = "roads.shp"
schools_fp = "schools_tartu.shp"

# Read files
grid = gpd.read_file(grid_fp)
roads = gpd.read_file(roads_fp)
schools = gpd.read_file(schools_fp)

# Re-project to WGS84
grid['geometry'] = grid['geometry'].to_crs(epsg=4326)
roads['geometry'] = roads['geometry'].to_crs(epsg=4326)
schools['geometry'] = schools['geometry'].to_crs(epsg=4326)

# Make a selection (only data above 0 and below 1000)
grid = grid.loc[(grid['Population'] > 0)]

# Create a Geo-id which is needed by the Folium (it needs to have a unique identifier for each row)
grid['geoid'] = grid.index.astype(str)
roads['geoid'] = roads.index.astype(str)
schools['geoid'] = schools.index.astype(str)

# Select data
grid = grid[['geoid', 'Population', 'geometry']]
roads = roads[['geoid', 'TYYP', 'geometry']]
schools = schools[['geoid', 'name', 'geometry']]

# convert the dataframe to geojson
grid_jsontxt = grid.to_json()
roads_jsontxt = roads.to_json()
schools_jsontxt = schools.to_json()


In [25]:
m = folium.Map(location=[58.37, 26.72], zoom_start=11, control_scale=True)

folium.GeoJson(grid_jsontxt).add_to(m)
folium.GeoJson(roads_jsontxt).add_to(m)
folium.GeoJson(schools_jsontxt).add_to(m)

m

In [26]:
m = folium.Map(location=[58.37, 26.72], tiles='Stamen terrain', zoom_start=8, control_scale=True, prefer_canvas=True, width=600, height=450)

# create a basic choropleth map, just polygons with some style information
folium.Choropleth(
    geo_data=grid_jsontxt,
    fill_color='red',
    fill_opacity=0.3,
    line_weight=1,
).add_to(m)

folium.LayerControl(collapsed=True).add_to(m)


In [27]:
m

In [28]:
import pysal.viz.mapclassify as mc

# Initialize the classifier and apply it
classifier = mc.NaturalBreaks.make(k=5)

grid['pop_km2'] = grid[['Population']].apply(classifier)
    
m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen terrain',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# Create Choropleth map where the colors are coming from a column "Population".
# Notice: 'geoid' column that we created earlier needs to be assigned always as the first column
# with threshold_scale we can adjust the class intervals for the values

choropleth = folium.Choropleth(
    geo_data=grid_jsontxt,
    data=grid,
    columns=['geoid', 'pop_km2'],
    key_on="feature.id",
    fill_opacity=0.5,
    line_opacity=0.2,
    line_color='white',
    line_weight=0,
    legend_name='Population classified Natural Breaks in Tartu',
    name='Population Grid',
    highlight=False,
    fill_color='RdBu'
)

choropleth.add_to(m)

folium.LayerControl(collapsed=True).add_to(m)

m

In [29]:
def getLinesAsPointList(row, geom):
    """Returns a list of coordinate pair tuples for the line ('lat', 'lon') of a LineString geometry"""
    if isinstance(row[geom], MultiLineString):
        return []
    else:
        list_x = list(row[geom].coords.xy[0])
        list_y = list(row[geom].coords.xy[1])
        # we need lat lon order for the folium map!!!
        return list(zip(list_y, list_x))

# Calculate x and y coordinates of the line
roads['points_list'] = roads.apply(getLinesAsPointList, geom='geometry', axis=1)

# list of lat lon coordinate pair tuples
# roadpoints = [a for a in roads['points_list'].tolist() if len(a) >=2 ]
roadpoints = []
for a in roads['points_list'].tolist():
    if len(a) >=2:
        roadpoints.append(a)
    
for road in roadpoints:
    folium.PolyLine(locations=road, color="grey", weight=2.5, opacity=1).add_to(m)

m

In [30]:
from shapely.geometry import Point

def getPoints(row, geom):
    """Returns coordinate pair tuples for the point ('lat', 'lon') of a Point geometry"""
    if isinstance(row[geom], Point):
        # we need lat lon order for the folium map!!!
        return (row[geom].y, row[geom].x)
    else:
        return ()


m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen terrain',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# Calculate x and y coordinates of the line
schools['points_tuple'] = schools.apply(getPoints, geom='geometry', axis=1)
    
for idx, school in schools.iterrows():
    folium.CircleMarker(location=school['points_tuple'], popup=school['name'], color="yellow", radius=2.5, opacity=0.9).add_to(m)


In [31]:
m

In [32]:
outfp = "folium_better_circle.html"

# Save the map
m.save(outfp)

In [33]:
from folium.plugins import MarkerCluster

# Get lat and lon of points
latlon = [[tup[0], tup[1]] for tup in schools['points_tuple'].tolist()]

m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen terrain',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# This function creates clusters for the points that are in the same area
# and then places them on the map
MarkerCluster(locations=latlon, fill_color='#2b8cbe', name="Schools", number_of_sides=6, radius=6).add_to(m)

folium.LayerControl().add_to(m)

In [34]:
m

In [14]:
from folium.plugins import MarkerCluster

# Get schools name information
names = schools['name'].tolist()

m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen terrain',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# This function creates clusters for the points that are in the same area
marker_cluster = MarkerCluster(name="Schools", number_of_sides=6, radius=6)

# and then places them in the marker cluster
for idx, school in schools.iterrows():
    folium.Marker(location=school['points_tuple'],
                        popup=school['name'],
                        color="yellow",
                        radius=5,
                        opacity=0.9).add_to(marker_cluster)


marker_cluster.add_to(m)

folium.LayerControl().add_to(m)

In [15]:
m

In [35]:
from folium.plugins import HeatMap
import numpy as np

random_weights = np.random.randint(low=1, high=10, size=len(schools))

heat_data = []

# Get lat and lon of points
for idx, row in schools.iterrows():
    tup = row['points_tuple']
    elem = [tup[0], tup[1], int(random_weights[idx])]
    heat_data.append(elem)

m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen toner',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# This function creates the heatmap based on the points and weights that are in close area
# and then places them on the map
HeatMap(data=heat_data,
        name="schools density",
        min_opacity=0.5,
        max_zoom=18,
        max_val=1.0,
        radius=25,
        blur=15,
        overlay=True,
        control=True).add_to(m)


folium.LayerControl().add_to(m)

m

In [36]:
# basemap
m = folium.Map(location=[58.37, 26.72],
               tiles='Stamen toner',
               zoom_start=8,
               control_scale=True,
               prefer_canvas=True,
               width=600,
               height=450)

# coloured polygon layer
folium.Choropleth(
    geo_data=grid_jsontxt,
    data=grid,
    columns=['geoid', 'pop_km2'],
    key_on="feature.id",
    fill_color='RdBu',
    fill_opacity=0.5,
    line_opacity=0.2,
    line_color='white',
    line_weight=0,
    legend_name='Population in Tartu',
    name='Population Grid',
    highlight=False
).add_to(m)

# heatmap layer
HeatMap(data=heat_data,
        name="schools density",
        min_opacity=0.5,
        max_zoom=18,
        max_val=1.0,
        radius=25,
        blur=15,
        overlay=True,
        control=True).add_to(m)

roads_layer = folium.FeatureGroup(name="roads layer")

# roads
for road in roadpoints:
    folium.PolyLine(locations=road, color="grey", weight=2.5, opacity=1).add_to(roads_layer)

roads_layer.add_to(m)

# This function creates clusters for the points that are in the same area
marker_cluster = MarkerCluster(name="Schools marker cluster", number_of_sides=6, radius=6)

# and then places them in the marker cluster
for idx, school in schools.iterrows():
    folium.Marker(location=school['points_tuple'],
                        popup=school['name'],
                        color="yellow",
                        radius=5,
                        opacity=0.9).add_to(marker_cluster)


marker_cluster.add_to(m)


circles_layer = folium.FeatureGroup(name="circles layer")

# the yellow school circles as reference
for idx, school in schools.iterrows():
    folium.CircleMarker(location=school['points_tuple'],
                        popup=school['name'],
                        color="yellow",
                        radius=2.5,
                        opacity=0.9).add_to(circles_layer)

circles_layer.add_to(m)

# the layer control switch
folium.LayerControl().add_to(m)


In [38]:
# Filepath to the output
outfp = "full_map.html"

# Save the map
m.save(outfp)

In [37]:
m